In [4]:
import numpy as np
import pandas as pd
import xgboost as xgb
import sklearn.metrics

In [5]:
nround     = 200
repeat     = 10
operator   = 4
newfeature = 64
numcv      = 10
param = {'bst:eta':0.02, 
         'silent' : 1,
         'objective':'binary:logistic',
         'bst:max_depth':11,
         'base_score':0.5,
         'subsample':0.9,
         'bst:colsample_bytree':0.5,
         'scale_pos_weight':1,
         'min_child_weight':5}
plst = param.items()
plst +=  [('eval_metric', 'auc')]
head = []
for i in range(64):
    head.append('X' + str(i+1))
head.append('Y')
Data = []
for i in range(5):
    temp = pd.read_csv('CSV/' + str(i+1) + 'year.csv', names = head, header = None, na_values = '?')
    temp = temp.fillna(temp.median())
    Data.append(temp)

In [6]:
for i in range(5):
    
    data = Data[i]
    cv = np.random.randint(numcv, size = data.shape[0])
    resultauc = pd.DataFrame(index = range(numcv), columns = range(repeat+2))
    
    for j in range(numcv):
        
        train  = data[cv != j]
        test   = data[cv == j]
        trainy = train['Y'].copy()
        trainx = train.drop(['Y'], axis = 1)
        testy  = test['Y'].copy()
        testx  = test.drop(['Y'], axis = 1)
        
        train  = xgb.DMatrix(trainx, label = trainy)
        test   = xgb.DMatrix(testx, label = testy)
        evallist           = [(test,'test'), (train,'train')]       
        bst                = xgb.train(plst, train, nround, evallist, early_stopping_rounds = 100)
        resultauc.loc[j,0] = float(bst.eval(test,'test',0).split(":")[1])
        
        p                  = np.zeros((trainx.shape[1]),dtype = float) + 1/float(trainx.shape[1])
        p_test             = pd.DataFrame(index = range(testx.shape[0]), columns = range(repeat), dtype = float)
        
        for k in range(repeat):
            
            for f in range(newfeature):
                
                o  = np.random.randint(operator, size = 1);
                f1 = np.random.multinomial(1, p, size = 1)[0]
                f2 = np.random.multinomial(1, p, size = 1)[0]
                
                if(o == 0):
                    c = '(' + trainx.columns[f1 == 1][0] + ')+(' + trainx.columns[f2 == 1][0] + ')'
                    if c not in trainx.columns:
                        trainx[c] = trainx[trainx.columns[f1 == 1][0]] + trainx[trainx.columns[f2 == 1][0]]
                        testx[c]  = testx[testx.columns[f1 == 1][0]] + testx[testx.columns[f2 == 1][0]]
                        p         = np.append(p,[0], axis = 0)
                elif(o == 1):
                    c = '(' + trainx.columns[f1 == 1][0] + ')-(' + trainx.columns[f2 == 1][0] + ')'
                    if c not in trainx.columns:
                        trainx[c] = trainx[trainx.columns[f1 == 1][0]] - trainx[trainx.columns[f2 == 1][0]]
                        testx[c]  = testx[testx.columns[f1 == 1][0]] - testx[testx.columns[f2 == 1][0]]
                        p         = np.append(p,[0], axis = 0)
                elif(o == 2):
                    c = '(' + trainx.columns[f1 == 1][0] + ')*(' + trainx.columns[f2 == 1][0] + ')'
                    if c not in trainx.columns:
                        trainx[c] = trainx[trainx.columns[f1 == 1][0]] * trainx[trainx.columns[f2 == 1][0]]
                        testx[c]  = testx[testx.columns[f1 == 1][0]] * testx[testx.columns[f2 == 1][0]]
                        p         = np.append(p,[0], axis = 0)
                else:
                    c = '(' + trainx.columns[f1 == 1][0] + ')/(' + trainx.columns[f2 == 1][0] + ')'
                    if c not in trainx.columns:
                        trainx[c] = trainx[trainx.columns[f1 == 1][0]] / trainx[trainx.columns[f2 == 1][0]]
                        testx[c]  = testx[testx.columns[f1 == 1][0]] / testx[testx.columns[f2 == 1][0]]
                        p         = np.append(p,[0], axis = 0) 
                
            trainx = trainx.fillna(0)
            testx  = testx.fillna(0)
            train  = xgb.DMatrix(trainx, label = trainy)
            test   = xgb.DMatrix(testx, label = testy)
            evallist           = [(test,'test'), (train,'train')]
            bst                = xgb.train(plst, train, nround, evallist, early_stopping_rounds = 100)
            resultauc.loc[j,k+1]   = float(bst.eval(test,'test',0).split(":")[1]) 
            p_test[k]          = bst.predict(test, ntree_limit = bst.best_ntree_limit)

            fscore             = bst.get_fscore()
            keys               = fscore.keys()
            features           = {}
            for key in keys:
                if(float(fscore[key]) >= np.percentile(fscore.values(), 50)):
                    features[key] = float(fscore[key])
            keys               = features.keys()
            
            p = np.zeros((len(keys)),dtype = float)
            trainnew = pd.DataFrame()
            testnew = pd.DataFrame()
            for m in range(len(keys)):
                key = keys[m]
                newtrain = trainx[key].copy()
                newtest  = testx[key].copy()
                trainnew = pd.concat([trainnew, newtrain], axis = 1)
                testnew  = pd.concat([testnew, newtest], axis = 1)
                p[m] = float(fscore[key])
                
            trainx = trainnew
            testx = testnew
            p = p/np.sum(p)
            features = pd.Series(p, index = keys)
            features = features.sort_values(ascending = False)
            features.to_csv('Result/' + str(i+1) + 'year' + str(j+1) + 'cv' + str(k+1) + 'repeat.csv')
            
        p_test.to_csv("Result/" + str(i+1) + "year" + str(j+1) + "cv.csv")
        p_mean = p_test.mean(1)
        auc = sklearn.metrics.roc_auc_score(testy, p_mean)
        resultauc.loc[j, repeat + 1] = auc
        
    resultauc.to_csv("Result/" + str(i+1) + 'yearAuc.csv')

[0]	test-auc:0.65373	train-auc:0.762381
Multiple eval metrics have been passed: 'train-auc' will be used for early stopping.

Will train until train-auc hasn't improved in 100 rounds.
[1]	test-auc:0.768064	train-auc:0.857871
[2]	test-auc:0.856844	train-auc:0.937871
[3]	test-auc:0.867271	train-auc:0.947079
[4]	test-auc:0.88148	train-auc:0.962403
[5]	test-auc:0.899178	train-auc:0.96535
[6]	test-auc:0.898627	train-auc:0.973812
[7]	test-auc:0.905383	train-auc:0.97371
[8]	test-auc:0.898921	train-auc:0.977345
[9]	test-auc:0.909752	train-auc:0.981925
[10]	test-auc:0.901821	train-auc:0.984564
[11]	test-auc:0.924218	train-auc:0.987113
[12]	test-auc:0.919885	train-auc:0.98853
[13]	test-auc:0.922823	train-auc:0.990458
[14]	test-auc:0.925173	train-auc:0.992867
[15]	test-auc:0.926274	train-auc:0.993963
[16]	test-auc:0.923043	train-auc:0.994912
[17]	test-auc:0.928183	train-auc:0.995358
[18]	test-auc:0.925099	train-auc:0.996257
[19]	test-auc:0.923777	train-auc:0.99681
[20]	test-auc:0.923557	train-auc

[3]	test-auc:0.878396	train-auc:0.949106
[4]	test-auc:0.8741	train-auc:0.95644
[5]	test-auc:0.867051	train-auc:0.961116
[6]	test-auc:0.887685	train-auc:0.96863
[7]	test-auc:0.905933	train-auc:0.97798
[8]	test-auc:0.913277	train-auc:0.980109
[9]	test-auc:0.943751	train-auc:0.986028
[10]	test-auc:0.947496	train-auc:0.990318
[11]	test-auc:0.943971	train-auc:0.99122
[12]	test-auc:0.958731	train-auc:0.992126
[13]	test-auc:0.966368	train-auc:0.993807
[14]	test-auc:0.962109	train-auc:0.995023
[15]	test-auc:0.961742	train-auc:0.995797
[16]	test-auc:0.959025	train-auc:0.996331
[17]	test-auc:0.959686	train-auc:0.997056
[18]	test-auc:0.96512	train-auc:0.997389
[19]	test-auc:0.960934	train-auc:0.997831
[20]	test-auc:0.962843	train-auc:0.998407
[21]	test-auc:0.968498	train-auc:0.998855
[22]	test-auc:0.969452	train-auc:0.999107
[23]	test-auc:0.972389	train-auc:0.99917
[24]	test-auc:0.973124	train-auc:0.999316
[25]	test-auc:0.971875	train-auc:0.999429
[26]	test-auc:0.969673	train-auc:0.999587
[27]	te

[50]	test-auc:0.950433	train-auc:1
[51]	test-auc:0.95271	train-auc:1
[52]	test-auc:0.954178	train-auc:1
[53]	test-auc:0.953297	train-auc:1
[54]	test-auc:0.951755	train-auc:1
[55]	test-auc:0.950286	train-auc:1
[56]	test-auc:0.949111	train-auc:1
[57]	test-auc:0.95014	train-auc:1
[58]	test-auc:0.951168	train-auc:1
[59]	test-auc:0.952636	train-auc:1
[60]	test-auc:0.95271	train-auc:1
[61]	test-auc:0.954105	train-auc:1
[62]	test-auc:0.953958	train-auc:1
[63]	test-auc:0.952857	train-auc:1
[64]	test-auc:0.953517	train-auc:1
[65]	test-auc:0.952857	train-auc:1
[66]	test-auc:0.953958	train-auc:1
[67]	test-auc:0.954545	train-auc:1
[68]	test-auc:0.954545	train-auc:1
[69]	test-auc:0.955059	train-auc:1
[70]	test-auc:0.954692	train-auc:1
[71]	test-auc:0.955573	train-auc:1
[72]	test-auc:0.955427	train-auc:1
[73]	test-auc:0.9555	train-auc:1
[74]	test-auc:0.957262	train-auc:1
[75]	test-auc:0.95763	train-auc:1
[76]	test-auc:0.958658	train-auc:1
[77]	test-auc:0.958805	train-auc:1
[78]	test-auc:0.959686	tra

[121]	test-auc:0.95293	train-auc:1
[122]	test-auc:0.952563	train-auc:1
[123]	test-auc:0.952636	train-auc:1
[124]	test-auc:0.951902	train-auc:1
[125]	test-auc:0.951535	train-auc:1
[126]	test-auc:0.952196	train-auc:1
[127]	test-auc:0.951314	train-auc:1
[128]	test-auc:0.951241	train-auc:1
[129]	test-auc:0.952049	train-auc:1
[130]	test-auc:0.951755	train-auc:1
[131]	test-auc:0.952416	train-auc:1
[132]	test-auc:0.951682	train-auc:1
[133]	test-auc:0.951168	train-auc:1
[134]	test-auc:0.950507	train-auc:1
[135]	test-auc:0.95058	train-auc:1
[136]	test-auc:0.951314	train-auc:1
[137]	test-auc:0.952636	train-auc:1
[138]	test-auc:0.95315	train-auc:1
[139]	test-auc:0.952049	train-auc:1
[140]	test-auc:0.951975	train-auc:1
[141]	test-auc:0.954325	train-auc:1
[142]	test-auc:0.954399	train-auc:1
[143]	test-auc:0.953885	train-auc:1
[144]	test-auc:0.954178	train-auc:1
Stopping. Best iteration:
[44]	test-auc:0.952489	train-auc:1

[0]	test-auc:0.770194	train-auc:0.809502
Multiple eval metrics have been pass

[34]	test-auc:0.928918	train-auc:0.999979
[35]	test-auc:0.928991	train-auc:0.999984
[36]	test-auc:0.927082	train-auc:0.999986
[37]	test-auc:0.927816	train-auc:0.999992
[38]	test-auc:0.926054	train-auc:0.999993
[39]	test-auc:0.927596	train-auc:0.999996
[40]	test-auc:0.922088	train-auc:0.999997
[41]	test-auc:0.92341	train-auc:0.999997
[42]	test-auc:0.920106	train-auc:1
[43]	test-auc:0.918931	train-auc:1
[44]	test-auc:0.915847	train-auc:1
[45]	test-auc:0.914819	train-auc:1
[46]	test-auc:0.91313	train-auc:1
[47]	test-auc:0.9157	train-auc:1
[48]	test-auc:0.919298	train-auc:1
[49]	test-auc:0.919959	train-auc:1
[50]	test-auc:0.922456	train-auc:1
[51]	test-auc:0.921428	train-auc:1
[52]	test-auc:0.920473	train-auc:1
[53]	test-auc:0.921134	train-auc:1
[54]	test-auc:0.919665	train-auc:1
[55]	test-auc:0.919445	train-auc:1
[56]	test-auc:0.92084	train-auc:1
[57]	test-auc:0.918931	train-auc:1
[58]	test-auc:0.920546	train-auc:1
[59]	test-auc:0.919151	train-auc:1
[60]	test-auc:0.919739	train-auc:1
[61]

...

[27]	test-auc:0.946078	train-auc:0.999805
[28]	test-auc:0.947812	train-auc:0.999856
[29]	test-auc:0.94995	train-auc:0.999882
[30]	test-auc:0.951039	train-auc:0.999907
[31]	test-auc:0.952087	train-auc:0.999935
[32]	test-auc:0.952974	train-auc:0.999949
[33]	test-auc:0.952853	train-auc:0.999969
[34]	test-auc:0.953983	train-auc:0.999971
[35]	test-auc:0.954023	train-auc:0.999982
[36]	test-auc:0.953539	train-auc:0.999989
[37]	test-auc:0.954668	train-auc:0.999989
[38]	test-auc:0.95729	train-auc:0.999993
[39]	test-auc:0.956846	train-auc:0.999994
[40]	test-auc:0.955435	train-auc:0.999992
[41]	test-auc:0.955152	train-auc:0.999995
[42]	test-auc:0.955193	train-auc:0.999997
[43]	test-auc:0.954225	train-auc:0.999997
[44]	test-auc:0.955314	train-auc:0.999998
[45]	test-auc:0.955757	train-auc:0.999998
[46]	test-auc:0.955838	train-auc:0.999999
[47]	test-auc:0.956362	train-auc:0.999999
[48]	test-auc:0.956967	train-auc:0.999999
[49]	test-auc:0.957088	train-auc:0.999999
[50]	test-auc:0.956644	train-auc:0.9

[90]	test-auc:0.936439	train-auc:1
[91]	test-auc:0.936076	train-auc:1
[92]	test-auc:0.936519	train-auc:1
[93]	test-auc:0.935068	train-auc:1
[94]	test-auc:0.935511	train-auc:1
[95]	test-auc:0.935148	train-auc:1
[96]	test-auc:0.936197	train-auc:1
[97]	test-auc:0.9366	train-auc:1
[98]	test-auc:0.936519	train-auc:1
[99]	test-auc:0.936157	train-auc:1
[100]	test-auc:0.935955	train-auc:1
[101]	test-auc:0.935189	train-auc:1
[102]	test-auc:0.934987	train-auc:1
[103]	test-auc:0.934342	train-auc:1
[104]	test-auc:0.934059	train-auc:1
[105]	test-auc:0.933656	train-auc:1
[106]	test-auc:0.933616	train-auc:1
[107]	test-auc:0.933454	train-auc:1
[108]	test-auc:0.933333	train-auc:1
[109]	test-auc:0.932809	train-auc:1
[110]	test-auc:0.931478	train-auc:1
[111]	test-auc:0.931559	train-auc:1
[112]	test-auc:0.931841	train-auc:1
[113]	test-auc:0.932164	train-auc:1
[114]	test-auc:0.932728	train-auc:1
[115]	test-auc:0.931801	train-auc:1
[116]	test-auc:0.93297	train-auc:1
[117]	test-auc:0.932204	train-auc:1
[118]

[8]	test-auc:0.925388	train-auc:0.988726
[9]	test-auc:0.929361	train-auc:0.991598
[10]	test-auc:0.93531	train-auc:0.993178
[11]	test-auc:0.934624	train-auc:0.993929
[12]	test-auc:0.935552	train-auc:0.994973
[13]	test-auc:0.934785	train-auc:0.995978
[14]	test-auc:0.938052	train-auc:0.996716
[15]	test-auc:0.941883	train-auc:0.997202
[16]	test-auc:0.943214	train-auc:0.998004
[17]	test-auc:0.942246	train-auc:0.99834
[18]	test-auc:0.943093	train-auc:0.998805
[19]	test-auc:0.94265	train-auc:0.998807
[20]	test-auc:0.945836	train-auc:0.999041
[21]	test-auc:0.944384	train-auc:0.999222
[22]	test-auc:0.948135	train-auc:0.999324
[23]	test-auc:0.951321	train-auc:0.999474
[24]	test-auc:0.951966	train-auc:0.99956
[25]	test-auc:0.954346	train-auc:0.999648
[26]	test-auc:0.955878	train-auc:0.999769
[27]	test-auc:0.955193	train-auc:0.999809
[28]	test-auc:0.954668	train-auc:0.999863
[29]	test-auc:0.957249	train-auc:0.999896
[30]	test-auc:0.958217	train-auc:0.99989
[31]	test-auc:0.95737	train-auc:0.999931


[58]	test-auc:0.914741	train-auc:1
[59]	test-auc:0.915064	train-auc:1
[60]	test-auc:0.914539	train-auc:1
[61]	test-auc:0.916354	train-auc:1
[62]	test-auc:0.916596	train-auc:1
[63]	test-auc:0.915789	train-auc:1
[64]	test-auc:0.916394	train-auc:1
[65]	test-auc:0.915386	train-auc:1
[66]	test-auc:0.914055	train-auc:1
[67]	test-auc:0.915991	train-auc:1
[68]	test-auc:0.915225	train-auc:1
[69]	test-auc:0.914983	train-auc:1
[70]	test-auc:0.914257	train-auc:1
[71]	test-auc:0.913894	train-auc:1
[72]	test-auc:0.913894	train-auc:1
[73]	test-auc:0.914055	train-auc:1
[74]	test-auc:0.913571	train-auc:1
[75]	test-auc:0.913894	train-auc:1
[76]	test-auc:0.914943	train-auc:1
[77]	test-auc:0.915749	train-auc:1
[78]	test-auc:0.916999	train-auc:1
[79]	test-auc:0.917282	train-auc:1
[80]	test-auc:0.917967	train-auc:1
[81]	test-auc:0.916959	train-auc:1
[82]	test-auc:0.918008	train-auc:1
[83]	test-auc:0.919419	train-auc:1
[84]	test-auc:0.919177	train-auc:1
[85]	test-auc:0.918532	train-auc:1
[86]	test-auc:0.9181

[128]	test-auc:0.913975	train-auc:1
[129]	test-auc:0.913894	train-auc:1
[130]	test-auc:0.91462	train-auc:1
[131]	test-auc:0.914822	train-auc:1
[132]	test-auc:0.915346	train-auc:1
[133]	test-auc:0.914943	train-auc:1
[134]	test-auc:0.915265	train-auc:1
[135]	test-auc:0.915144	train-auc:1
[136]	test-auc:0.916031	train-auc:1
[137]	test-auc:0.915507	train-auc:1
[138]	test-auc:0.915668	train-auc:1
[139]	test-auc:0.916677	train-auc:1
[140]	test-auc:0.916233	train-auc:1
[141]	test-auc:0.91712	train-auc:1
Stopping. Best iteration:
[41]	test-auc:0.921718	train-auc:1

